# Analyse non paramétrique du signal

Nous allons commencer par afficher le signals

/TODO mettre des labels X/Y avec unités et des titres à toutes les figure

/TODO ajouter les fenêtres dans la fonction fft

/TODO analyse paramétrique avec sinus cardinal

In [1]:
using WAV # Wavread
using Plots # Plot
using FFTW #Fft
using DSP # Fftfreq
using WORLD # Harvest
using PyPlot # Imshow

In [41]:
s_, fs_ = wavread("../myson.wav");
s_ = vec(s_);
t_ = (0 : 1 : size(s_)[1]-1)/fs_;
fs_ = floor(Int, fs_);

t_s_ = 10 #s
trame_period_ = 0.004 #s0.1

floor_freq_ = 10 #Hz
ceil_freq_ = 1000 #Hz

number_trame_ = 50 # trames on each side of t_s
overlap_ = 0.000001#s

N_fft_ = 2^17 - 1; #number points fft

In [3]:
#plot(t, s, title="Son bizarre",label=["Signal"])

Regardons des trames. La taille de trame reste classique : de l'ordre de 20ms.

/TODO attention Gabor

/TODO FFT avec gros nombre

In [4]:
function signal_trame(time_axis, signal, t_start, delta_trame, fsampling, number_of_trames=1)
    i_s = floor(Int, t_start*fsampling-number_of_trames*delta_trame*fsampling/2+1)
    i_e = floor(Int, i_s+number_of_trames*delta_trame*fsampling)
    t_trame = time_axis[i_s:i_e]
    s_trame = signal[i_s:i_e]
    return [t_trame, s_trame]
end

function plot_fft(time_axis, signal, fsampling, N_fft, floor_f, ceil_f)
    # Fourier Transform of it 
    s_pad = zeros(N_fft)
    s_pad[1:size(signal,1), 1:size(signal,2)]=signal
    F = fft(s_pad) |> fftshift
    freqs = fftfreq(N_fft, fsampling) |> fftshift

    # plots 
    time_domain = Plots.plot(time_axis, signal, title = "Signal")
    freq_domain = Plots.plot(freqs, abs.(F), title = "Spectrum", xlim=(floor_f, ceil_f)) 
    Plots.plot(time_domain, freq_domain, layout = 2)
end

plot_fft (generic function with 1 method)

In [42]:
t_trame_, s_trame_ = signal_trame(t_, s_, t_s_, trame_period_, fs_, 1)
plot_fft(t_trame_, s_trame_, fs_, N_fft_, floor_freq_, ceil_freq_)

In [6]:
t_trame_long_, s_trame_long_ = signal_trame(t_, s_, t_s_, trame_period_, fs_, 4)
plot_fft(t_trame_long_, s_trame_long_, fs_, N_fft_, floor_freq_, ceil_freq_)

On cherche maintenant la fréquence du fondamental. Comme il s'agit d'un instrument à vent, on choisit notre interval de fréquence.

In [7]:
#f0_, timeaxis_ = harvest(s_, fs_, HarvestOption(floor_freq_, ceil_freq_, trame_period_));#floor and ceil freq, period
#plot(timeaxis_, f0_)

On observe des vibratos, par exemple un gros vibrato vers 5s, un "fa". La fréquence du son ne correspond pas exactement à la fréquence du fondamental. On a une modulation de fréquence.

/TODO étudier cette modulation de fréquence

Regardons un zoom sur un vibrato. 

/TODO fft du petit bout de signal

In [8]:
#f0_trame_, timeaxis_trame_ = harvest(s_trame_, fs_, HarvestOption(floor_freq_, ceil_freq_, trame_period_));
#plot(timeaxis_trame_.+t_trame_[1], f0_trame_)

In [9]:
#f0_trame_long_, timeaxis_trame_long_ = harvest(s_trame_long_, fs_, HarvestOption(floor_freq_, ceil_freq_, trame_period_));
#plot(timeaxis_trame_long_.+t_trame_long_[1], f0_trame_long_)

On va s'intéresser maintenant au spectrogramme.

\TODO On choisit une fenêtre XXXX car XXX

In [20]:
function plot_spectrogram(t_shift, signal, fsampling, ceil_f, floor_f, delta_trame, delta_overlap, N_fft, windows_spectro)
    S = spectrogram(signal, floor(Int, delta_trame*fsampling), floor(Int, 0.01*delta_overlap*fsampling); nfft=N_fft, fs=fsampling, window=windows_spectro)
    t = time(S)
    f = freq(S)
    i_f_min = floor(Int, floor_f/(last(f)-first(f))*size((power(S))[:, 1])[1])
    i_f_max = ceil(Int, ceil_f/(last(f)-first(f))*size((power(S))[:, 1])[1])
    PyPlot.imshow(reverse(log10.(power(S)[i_f_min:i_f_max, :]), dims=1), extent=[first(t)+t_shift, last(t)+t_shift, floor_f, ceil_f], aspect="auto")
end

plot_spectrogram (generic function with 1 method)

In [ ]:
plot_spectrogram(0, s_, fs_, ceil_freq_, floor_freq_, trame_period_, overlap_, N_fft_, hanning)

Zoom sur notre vibrato que l'on voit un peu

In [13]:
using WORLD
aperiodicity = d4c(s_trame, fs, timeaxis, f0)
imshow(aperiodicity)

UndefVarError: UndefVarError: s_trame not defined